In [2]:
%reload_ext autoreload
%autoreload 2
sys.path.insert(0, '../../src/')
import pandas as pd
import sys
import data_loader
pd.set_option('display.max_columns', None)
import matplotlib.pyplot as plt
from pytablewriter import MediaWikiTableWriter
import plotly.express as px
from statsmodels.graphics.tsaplots import plot_acf
pd.options.plotting.backend = "plotly"
import plotly.graph_objects as go

In [53]:
player_data = data_loader.player_data_convert_to_metric_units(data_loader.load_player_data(seasons=None))

Loaded PBP-data
Loaded player-info data


In [462]:
fig = px.box(player_data[player_data["fg_attempts"]>400],notched=True,y=["difference_fg_percent_after_make_miss"], width=1000, height=800, hover_data=["player_name","season_name","fg_attempts"])
fig.update_layout(title_text="Box-plot of difference in per player and season shooting percentages for shots after make/miss:")
fig.show()

In [453]:
fig = px.box(player_data[player_data["fg_attempts"]>400],notched=True,y=["fg_percent_after_make","fg_percent_after_miss"], width=1200, height=800, hover_data=["player_name","season_name","fg_attempts"])
fig.update_layout(title_text="Box-plot of per player and season shooting percentages for shots after make/miss:")
fig.show()

In [410]:
player_data[player_data["fg_attempts"]>300]["streakyness"].describe()

count    4746.000000
mean       -0.013879
std         0.041721
min        -0.161286
25%        -0.040307
50%        -0.013892
75%         0.012488
max         0.154642
Name: streakyness, dtype: float64

In [459]:
player_data["fg_percent"] = player_data["fg_made"] / (player_data["fg_made"]+player_data["fg_missed"])
player_data["fg_attempts"] = (player_data["fg_made"]+player_data["fg_missed"])
player_data["ft_percent"] = player_data["ft_made"] / (player_data["ft_made"]+player_data["ft_missed"])
player_data["3PT_percent"] = player_data["3PT_made"] / (player_data["3PT_made"]+player_data["3PT_missed"])
player_data["2PT_percent"] = (player_data["fg_made"] - player_data["3PT_made"]) / (player_data["fg_made"] - player_data["3PT_made"]+player_data["fg_missed"]-player_data["3PT_missed"])
player_data["fg_percent_after_make"] = player_data["fg_made_after_make"] / (player_data["fg_made_after_make"]+player_data["fg_missed_after_make"])
player_data["fg_percent_after_miss"] = player_data["fg_made_after_miss"] / (player_data["fg_made_after_miss"]+player_data["fg_missed_after_miss"])
player_data["difference_fg_percent_after_make_miss"] = player_data["fg_percent_after_make"]-player_data["fg_percent_after_miss"]
player_data["streakyness_sign"] = player_data["streakyness"]>0
player_data["points_pg"] = player_data["points"]/player_data["games_played"]
player_data["assists_pg"] = player_data["assists"]/player_data["games_played"]
player_data["rebounds_pg"] = player_data["rebounds"]/player_data["games_played"]
player_data["production_pg"] = player_data["points_pg"] + player_data["assists_pg"] + player_data["rebounds_pg"]
player_data["fieldgoals_pg"] = player_data["fg_made"]/player_data["games_played"]
player_data["turnover_pg"] = player_data["turnover"]/player_data["games_played"]
player_data["fouls_pg"] = player_data["fouls"]/player_data["games_played"]
player_data["ft_attempts"] = player_data["ft_made"] + player_data["ft_missed"]
player_data["ftapg"] = player_data["ft_attempts"]/player_data["games_played"]
player_data["season"] = player_data["season_name"].str[:4]
player_data["fg_made_rounded"] = player_data["fg_made"].apply(lambda x: int(50 * round(float(x)/50)))
player_data["assist_per_turnover"] = (player_data["assists"] / player_data["turnover"])
player_data["name_season"] = player_data["player_name"] + " " + player_data["season"]

In [3]:
pbp_data = data_loader.load_data(seasons=None)

In [7]:
pbp_data = pbp_data[(pbp_data["EVENTMSGTYPE"]=="FIELD_GOAL_MADE")|(pbp_data["EVENTMSGTYPE"]=="FIELD_GOAL_MISSED")]

In [48]:
streaks = {}
for id, group in pbp_data.groupby(["season_name","PLAYER1_ID"]):
    max_make = 0
    current_make = 0
    max_miss = 0
    current_miss = 0
    for _,attempt in group.sort_values(["GAME_ID","PERIOD","PCTIMESTRING"],ascending=[True, True,False]).iterrows():
        if attempt["EVENTMSGTYPE"] == "FIELD_GOAL_MADE":
            current_miss = 0
            current_make += 1
        else:
            current_make = 0
            current_miss += 1
        if max_make<current_make:
            max_make = current_make
        if max_miss<current_miss:
            max_miss = current_miss
    streaks[f"{id[1]}:{group.iloc[0]['PLAYER1_NAME']}:{id[0]}"] = {"attempts": len(group),"make":max_make,"miss":max_miss}

In [51]:
pd.DataFrame(streaks).transpose().sort_values("miss").tail()

attempts  make  miss
2060:Marko Jaric:2008-09               145     3    22
202335:Patrick Patterson:2018-19       219     4    22
2693:Keith McLeod:2004-05              408     6    23
1747:Rafer Alston:2004-05              974     9    23
101207:Kevin Burleson:2005-06           88     4    36

In [47]:
pbp_data[(pbp_data["season_name"]=="2018-19")&(pbp_data["PLAYER1_NAME"]=="Serge Ibaka")].sort_values(["GAME_ID","PERIOD","PCTIMESTRING"],ascending=[True, True,False]).reset_index(drop=True).iloc[100:150]

Unnamed: 0                  EVENTMSGACTIONTYPE       EVENTMSGTYPE  \
100         278                           Jump Shot  FIELD_GOAL_MISSED   
101         428                           Jump Shot  FIELD_GOAL_MISSED   
102         484                           Jump Shot    FIELD_GOAL_MADE   
103          98                  Floating Jump Shot  FIELD_GOAL_MISSED   
104         102                           Jump Shot  FIELD_GOAL_MISSED   
105         106                   Cutting Dunk Shot    FIELD_GOAL_MADE   
106         138                           Jump Shot  FIELD_GOAL_MISSED   
107         162                           Jump Shot  FIELD_GOAL_MISSED   
108         166                               Layup    FIELD_GOAL_MADE   
109         299                           Jump Shot  FIELD_GOAL_MISSED   
110         303                           Jump Shot  FIELD_GOAL_MISSED   
111         314                           Hook Shot    FIELD_GOAL_MADE   
112         329                           Jump Shot    FIELD_GOAL_MADE   
113         357     Driving Floating Bank Jump Shot    FIELD_GOAL_MADE   
114         366                           Jump Shot    FIELD_GOAL_MADE   
115          18                           Jump Shot    FIELD_GOAL_MADE   
116          26                           Jump Shot    FIELD_GOAL_MADE   
117          43                           Jump Shot    FIELD_GOAL_MADE   
118          47                  Cutting Layup Shot    FIELD_GOAL_MADE   
119          59                           Hook Shot    FIELD_GOAL_MADE   
120          64                       Putback Layup    FIELD_GOAL_MADE   
121          67                        Driving Dunk    FIELD_GOAL_MADE   
122           9                           Jump Shot    FIELD_GOAL_MADE   
123         188                       Putback Layup    FIELD_GOAL_MADE   
124         207                        Running Dunk    FIELD_GOAL_MADE   
125         211                 Turnaround Fadeaway    FIELD_GOAL_MADE   
126         270                  Cutting Layup Shot    FIELD_GOAL_MADE   
127         276                   Cutting Dunk Shot    FIELD_GOAL_MADE   
128         292                       Putback Layup    FIELD_GOAL_MADE   
129         297                 Turnaround Fadeaway  FIELD_GOAL_MISSED   
130         320                                Dunk    FIELD_GOAL_MADE   
131         440                       Driving Layup  FIELD_GOAL_MISSED   
132          63                           Jump Shot    FIELD_GOAL_MADE   
133          76                  Floating Jump Shot    FIELD_GOAL_MADE   
134          86                           Jump Shot    FIELD_GOAL_MADE   
135          94                               Layup    FIELD_GOAL_MADE   
136         113                           Hook Shot    FIELD_GOAL_MADE   
137         333                    Pullup Jump Shot    FIELD_GOAL_MADE   
138         383  Turnaround Fadeaway Bank Jump Shot    FIELD_GOAL_MADE   
139         374                           Hook Shot    FIELD_GOAL_MADE   
140          30                           Jump Shot    FIELD_GOAL_MADE   
141          46                           Jump Shot    FIELD_GOAL_MADE   
142          14                   Driving Hook Shot  FIELD_GOAL_MISSED   
143         273                           Hook Shot    FIELD_GOAL_MADE   
144         284                           Jump Shot    FIELD_GOAL_MADE   
145         303                      Tip Layup Shot    FIELD_GOAL_MADE   
146         315                           Jump Shot  FIELD_GOAL_MISSED   
147         437                           Jump Shot  FIELD_GOAL_MISSED   
148         443                           Jump Shot    FIELD_GOAL_MADE   
149         469                           Jump Shot  FIELD_GOAL_MISSED   

     EVENTNUM   GAME_ID                               HOMEDESCRIPTION  \
100       419  21800100                      MISS Ibaka 19' Jump Shot   
101       640  21800100                      MISS Ibaka 16' Jump Shot   
102       7

In [335]:
player_data[(player_data["assist_per_turnover"]<100000000)&(player_data["games_played"].isin(range(0,82)))].groupby("games_played")["assist_per_turnover"].mean().plot(width=1200, height=800, range_y=[0,2], title="Assist-Turnover ratio by of games played")

In [216]:
fig = px.scatter(player_data[player_data["games_played"]>30], x="fg_percent", y="ft_percent", hover_data=["player_name","season_name"], width=800, height=800, trendline="ols")
fig.update_traces(
        marker_size=5, opacity=0.8)
fig.update_layout(title_text="Games by home and visitor net record:")
fig.show()

In [316]:
player_data[player_data["games_played"].isin(range(0,82))].groupby("games_played")[["ft_percent","2PT_percent","3PT_percent"]].agg("mean").plot(width=1200, height=800, range_y=[0,0.8], title="Mean shooting efficiency by games played")

In [304]:
player_data[player_data["games_played"].isin(range(0,82))].groupby("games_played")[["points_pg","rebounds_pg","assists_pg"]].agg("mean").plot(width=1200, height=800, title="Mean per game production by games played")

In [311]:
player_data[player_data["games_played"].isin(range(0,82))].groupby("games_played")[["fouls_pg","turnover_pg"]].agg("mean").plot(width=1200, height=800, title="Mean per game fouls/turnovers by games played", range_y=[0,3])

In [ ]:
fig = go.Figure()
fig.add_trace(go.Line(x=random_x, y=random_y0,
                    mode='lines',
                    name='lines'))
fig.add_trace(go.Scatter(x=random_x, y=random_y1,
                    mode='lines+markers',
                    name='lines+markers'))
fig.add_trace(go.Scatter(x=random_x, y=random_y2,
                    mode='markers', name='markers'))

fig.show()

In [361]:
fig = px.scatter(player_data[player_data["games_played"].isin(range(0,83))], x="games_played", y="production_pg", hover_data=["player_name","season_name"], text="name_season", width=1200, height=800, trendline="ols")
fig.update_traces(
        marker_size=5, opacity=0.8)
fig.update_traces(textposition='top center')
fig.data[0].text = [e if e in ["Kevin Durant 2014","Kevin Love 2012","Metta World Peace 2004", "DeMarcus Cousins 2017"] else '' for e in fig.data[0].text]
fig.data[0].text = ["Durant 2014 (Injury)" if e in ["Kevin Durant 2014"] else e for e in fig.data[0].text]
fig.data[0].text = ["Love 2012 (Injury)" if e in ["Kevin Love 2012"] else e for e in fig.data[0].text]
fig.data[0].text = ["Peace 2004 (Suspension)" if e in ["Metta World Peace 2004"] else e for e in fig.data[0].text]
fig.data[0].text = ["Cousins 2017 (Injury)" if e in ["DeMarcus Cousins 2017"] else e for e in fig.data[0].text]
fig.update_layout(title_text="Per game production by games played")
fig.show()

In [252]:
player_data[player_data["fg_made"].isin(range(50,800))].groupby("fg_made_rounded")["streakyness"].mean().plot()

In [284]:
player_data[(player_data["fg_made"].isin(range(50,500)))][["fg_percent","fg_percent_after_make","fg_percent_after_miss","streakyness_sign","fg_made_rounded"]].groupby("fg_made_rounded")["streakyness_sign"].mean().plot(width=800)

In [456]:
player_data[player_data["fg_attempts"]>=400].groupby("streakyness_sign").size()

streakyness_sign
False    2546
True     1365
dtype: int64

In [290]:
player_data[(player_data["fg_made"]>100)&(abs(player_data["streakyness"])>0.01)].groupby("streakyness_sign").size()

streakyness_sign
False    2905
True     1515
dtype: int64

In [473]:
player_data[player_data["player_name"]=="Tony Parker"]["difference_fg_percent_after_make_miss"].reset_index(drop=True).plot()

In [476]:
player_data[player_data["fg_attempts"]>=400].groupby("season")["difference_fg_percent_after_make_miss"].mean().plot()

In [420]:
player_data[player_data["fg_attempts"]>400].reset_index().groupby("index")["streakyness"].mean().sort_values()

index
21        -0.148217
123       -0.131633
1761      -0.124721
762       -0.121437
203144    -0.102138
             ...   
202361     0.081677
203894     0.082316
203526     0.085373
717        0.093511
1628386    0.099548
Name: streakyness, Length: 846, dtype: float64

In [432]:
player_data[["fg_made_after_make","fg_missed_after_make","fg_made_after_miss","fg_missed_after_miss"]].sum()

fg_made_after_make       769407
fg_missed_after_make     937315
fg_made_after_miss       936926
fg_missed_after_miss    1124599
dtype: int64